# Assignment 03

Caroline O’Sullivan (Boston University)  
September 20, 2025

In [1]:
from pyspark.sql import SparkSession
import pandas as pd
import plotly.express as px
import plotly.io as pio
import numpy as np
import plotly.graph_objects as go
import numpy as np

np.random.seed(42)

pio.renderers.default = "notebook+svg"

# Initialize Spark Session
spark = SparkSession.builder.appName("LightcastData").getOrCreate()

# Load Data
df = spark.read.option("header", "true").option("inferSchema", "true").option("multiLine","true").option("escape", "\"").csv("data/lightcast_job_postings.csv")

# Show Schema and Sample Data
#print("---This is Diagnostic check, No need to print it in the final doc---")

#df.printSchema() # comment this line when rendering the submission
#df.show(5)

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/09/20 14:35:04 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [2]:
#Data Preparation and Cleaning

df = df.withColumn("SALARY", df["SALARY"].cast("float"))\
        .withColumn("SALARY_TO", df["SALARY_TO"].cast("float"))\
        .withColumn("SALARY_FROM", df["SALARY_FROM"].cast("float"))\
        .withColumn("MIN_YEARS_EXPERIENCE", df["MIN_YEARS_EXPERIENCE"].cast("float"))\
        .withColumn("MAX_YEARS_EXPERIENCE", df["MAX_YEARS_EXPERIENCE"].cast("float"))
        
average_salary = df.agg({"SALARY": "avg"}).first()[0]
median_to_salary = df.approxQuantile("SALARY_TO", [0.5], 0.01)[0]
median_from_salary = df.approxQuantile("SALARY_FROM", [0.5], 0.01)[0]

df = df.fillna({"SALARY": average_salary,
                 "SALARY_TO": median_to_salary,
                 "SALARY_FROM": median_from_salary,})

df = df.withColumn("Average Salary", (df["SALARY_TO"] + df["SALARY_FROM"])/2)

export_cols = [
    "Average Salary", "SALARY", "SALARY_TO", "SALARY_FROM",
    "MIN_YEARS_EXPERIENCE", "MAX_YEARS_EXPERIENCE",
    "EMPLOYMENT_TYPE_NAME", "NAICS2_NAME", "EDUCATION_LEVELS_NAME"
]

df_selected = df.select(export_cols)
pdf = df_selected.toPandas()
pdf.to_csv("cleaned_lightcast_job_postings.csv", index=False)

In [5]:
#Salary Distribution by Industry and Employment Type
fig = px.box(
    pdf,
    x="EMPLOYMENT_TYPE_NAME",
    y="SALARY",
    title="Salary Distribution by Employment Type",
    color_discrete_sequence=["#C71585"],
    points="outliers",
)
fig.update_layout(
    font_family="Arial",
    title_font_size=16,
    xaxis_title="Employment Type",
    yaxis_title="Salary",
    xaxis_tickangle=-45,
)
fig.show()
fig.write_html("Q1.html")
fig.write_image("Q1.png")


![Salary Distribution By Employment Type](Q1.png)